<a href="https://colab.research.google.com/github/ark0723/tb_project/blob/main/fine_tuning.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Mount Google Deive

In [ ]:
from google.colab import drive
# Mount the Google Drive at /content/drive
drive.mount('/content/drive')

# Verify by listing the files in the drive
!ls /content/drive/My\ Drive/

Mounted at /content/drive
 aif_deploy.zip
 aws_keys
'AWS Training & Certification - Certificate of Completion.pdf'
 BE_02_Collabo_team_02.gsheet
 blog_ABTest.zip
'Colab Notebooks'
 dashboard.zip
 dataset
 django-youtube.zip
 DOCKER_FUNCODING_20230725
 iamport.zip
 jwt_logic.txt
 LLM.zip
 miniproject.zip
 mysql_install.pdf
 openai.zip
 oz_02_collabo-002-main.zip
 oz_02_collabo-004-BE-dev.zip
 oz_02_collabo-004-develop.zip
 oz_02_collabo-007-BE-develop.zip
 oz_02_main-003-BE-develop.zip
 oz_02_main-003-FE-dev.zip
 oz_02_main-004-BE.zip
 oz_02_main-004-FE-develop.zip
 oz_02_main-005-BE-comment.zip
 oz_02_main-005-BE-community.zip
 oz_02_main-005-BE-members.zip
 resume.zip
 RL
 yolo_train
'고아라 한 내용.gdoc'
 구글로그인
'기술면접 질문.gdoc'
'깃 셋팅 상세하게!.drawio'
'[오즈코딩스쿨] 휴가 신청서 양식 (백엔드)의 사본.gdoc'
 운영체제강의
'제목 없는 다이어그램 (1).drawio'
'제목 없는 다이어그램.drawio'
 추천시스템
'코딩관련 노트.gdoc'


# Hyper-parameter tuning
- https://docs.ultralytics.com/integrations/ray-tune/#how-can-i-integrate-weights-biases-with-my-yolo11-model-tuning

In [ ]:
# Install and update Ultralytics and Ray Tune packages
%pip install -U ultralytics "ray[tune]"

# Optionally install W&B for logging
%pip install wandb

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 877.5/877.5 kB 16.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 7.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 241.9/241.9 kB 18.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.0/66.0 MB 18.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.0/16.0 MB 97.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 12.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 314.5/314.5 kB 20.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 4.1 MB/s eta 0:00:00


In [ ]:
from ultralytics import YOLO
import ray
from ray import tune
# from ray.tune.search.nevergrad import NevergradSearch
from ray.tune.schedulers import ASHAScheduler
from ray.tune import CLIReporter
import wandb

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


In [ ]:
# Initialize the YOLO model
model = YOLO("yolo11n.pt")

# login to WandB
wandb.login(key = "8ce52eebbb47888d7b9a5b83ddfe0c17a56b1f24")

# Define search space
search_space = {
    "box": tune.uniform(7.5, 10.0),  # Box loss weight
    "cls": tune.uniform(0.2, 1.0),  # Class loss weight
    "lr0": tune.loguniform(1e-5, 1e-3),  # Learning rate for AdamW
    "imgsz": tune.choice([640, 1280]),      # Image size
}


# Define Ray Tune scheduler and reporter
scheduler = ASHAScheduler(
    metric="metrics/mAP50-95(B)",
    mode="max",
    max_t=50,  # epochs
    grace_period=10,
    reduction_factor=2
)

reporter = CLIReporter(
    parameter_columns=["box", "cls", "lr0", "imgsz"],
    metric_columns=["metrics/mAP50-95(B)", "bbox_loss"]
)

# Ray Tune objective function to tune hyperparameters
def tune_objective(config):
    # Train the model
    results = model.train(
        data="/content/drive/MyDrive/yolo_train/dataset/augmented_data.yaml",
        epochs=50,
        batch = 16,
        imgsz=config['imgsz'],
        optimizer="AdamW",
        lr0=config["lr0"],
        box=config["box"],
        cls=config["cls"],
        patience=10,
        save=False,  # Don't save the model during tuning
        plots=False,  # Disable plotting
        val=True,  # Disable validation to speed up the process
        project = "tb_yolo"
    )


# Run Ray Tune
analysis = tune.run(
    tune_objective,
    config=search_space,
    num_samples=50,  # Number of experiments to run
    scheduler=scheduler,
    progress_reporter=reporter,
    resources_per_trial=None,
    storage_path="/content/drive/MyDrive/ray_results",  # Directory to store tuning results
    name="yolo_tuning",
    time_budget_s=36000, # set time limit to 10 hours
    max_concurrent_trials= 20,
)

# Get the best hyperparameters from Ray Tune
best_config = analysis.best_config
print("Best hyperparameters found were: ", best_config)


100%|██████████| 5.35M/5.35M [00:00<00:00, 68.8MB/s]
wandb: Using wandb-core as the SDK backend. Please refer to https://wandb.me/wandb-core for more information.
wandb: W&B API key is configured. Use `wandb login --relogin` to force relogin
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
2024-10-25 10:01:47,877	INFO worker.py:1816 -- Started a local Ray instance.
2024-10-25 10:01:49,166	INFO tune.py:253 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `tune.run(...)`.
2024-10-25 10:01:49,754	WARNING tune.py:902 -- AIR_VERBOSITY is set, ignoring passed-in ProgressReporter for now.


+----------------------------------------------------------+
| Configuration for experiment     yolo_tuning             |
+----------------------------------------------------------+
| Search algorithm                 BasicVariantGenerator   |
| Scheduler                        AsyncHyperBandScheduler |
| Number of trials                 50                      |
+----------------------------------------------------------+

View detailed results here: /content/drive/MyDrive/ray_results/yolo_tuning
To visualize your results with TensorBoard, run: `tensorboard --logdir /tmp/ray/session_2024-10-25_10-01-46_065029_2517/artifacts/2024-10-25_10-01-49/yolo_tuning/driver_artifacts`
(raylet) Warning: The actor ImplicitFunc is very large (20 MiB). Check that its definition is not implicitly capturing a large array or other object in scope. Tip: use ray.put() to put large objects in the Ray object store.

Trial status: 20 PENDING
Current time: 2024-10-25 10:01:56. Total running time: 6s
Logical r

  0%|          | 0.00/755k [00:00<?, ?B/s]
100%|██████████| 755k/755k [00:00<00:00, 14.7MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.2MB/s]
100%|██████████| 755k/755k [00:00<00:00, 13.8MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.1MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.7MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.6MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.1MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.5MB/s]
100%|██████████| 755k/755k [00:00<00:00, 13.6MB/s]
100%|██████████| 755k/755k [00:00<00:00, 13.9MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.7MB/s]
100%|██████████| 755k/755k [00:00<00:00, 15.0MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.8MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.3MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.7MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.2MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.7MB/s]
100%|██████████| 755k/755k [00:00<00:00, 14.0MB/s]
100%|██████████| 755k/755k [00:00<00:00

(tune_objective pid=9568) Overriding model.yaml nc=80 with nc=45
(tune_objective pid=9568) 
(tune_objective pid=9568)                    from  n    params  module                                       arguments                     
(tune_objective pid=9568)   0                  -1  1       464  ultralytics.nn.modules.conv.Conv             [3, 16, 3, 2]                 
(tune_objective pid=9568)   1                  -1  1      4672  ultralytics.nn.modules.conv.Conv             [16, 32, 3, 2]                
(tune_objective pid=9568)   2                  -1  1      6640  ultralytics.nn.modules.block.C3k2            [32, 64, 1, False, 0.25]      
(tune_objective pid=9568)   3                  -1  1     36992  ultralytics.nn.modules.conv.Conv             [64, 64, 3, 2]                
(tune_objective pid=9568)   4                  -1  1     26080  ultralytics.nn.modules.block.C3k2            [64, 128, 1, False, 0.25]     
(tune_objective pid=9568)   5                  -1  1    147712  ultr

(tune_objective pid=9576) wandb: Currently logged in as: ark0723 (ark0723-university-of-arkansas). Use `wandb login --relogin` to force relogin


...

  0%|          | 0/8 [00:00<?, ?it/s]
      13/50         0G      0.694      3.789     0.8718        329       1280:  50%|█████     | 4/8 [02:49<02:51, 42.87s/it]


(tune_objective pid=42709) 
(tune_objective pid=42709)       Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


      13/50         0G     0.6038       1.11     0.8484        272       1280:  25%|██▌       | 2/8 [01:27<04:23, 43.85s/it]
      12/50         0G     0.5166      1.923     0.8428        307       1280:  12%|█▎        | 1/8 [00:49<05:46, 49.55s/it]



Trial status: 37 TERMINATED | 13 RUNNING
Current time: 2024-10-25 13:26:19. Total running time: 3hr 24min 30s
Logical resource usage: 13.0/96 CPUs, 0/0 GPUs (0.0/4.0 TPU, 0.0/1.0 accelerator_type:TPU-V2)
+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
| Trial name                   status           box        cls           lr0     imgsz     iter     total time (s)     metrics/precision(B)     metrics/recall(B)     metrics/mAP50(B)     metrics/mAP50-95(B) |
+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
| tune_objective_26c3f_00004   RUNNING      7.93897   0.959121   0.000131161      1280       22           12084.2                   0.76049               0.69616       

      13/50         0G     0.6622      3.601     0.8728        367       1280:  38%|███▊      | 3/8 [02:08<03:36, 43.25s/it] [repeated 4x across cluster]


##### 3. Saving the Best Hyperparameters
After running the tuning process, Ray Tune saves the results in the directory (~/ray_results/yolo_tuning/). You can manually save the best hyperparameters or export them for future use.

Example to save the best hyperparameters to a file:

In [ ]:
import json

# Save the best hyperparameters to a JSON file
with open("best_hyperparams.json", "w") as f:
    json.dump(best_config, f)

##### To load the tuned hyperparameters and apply them for a new training session, you can read the saved JSON file:

In [ ]:
# Load the best hyperparameters
with open("best_hyperparams.json", "r") as f:
    best_hyperparams = json.load(f)

# Use the best hyperparameters for training
model.train(
    data="/content/drive/MyDrive/yolo_train/dataset/augmented_data.yaml",
    epochs=100,
    batch=16,
    imgsz=best_hyperparams["imgsz"],
    optimizer="AdamW",
    lr0=best_hyperparams["lr0"],
    box=best_hyperparams["box"],
    cls=best_hyperparams["cls"],
    save=True,  # Save the model after tuning
    plots=True,
    val=True,
    patience=10
)


##### 5. Ray Tune Results Access and Analysis
Ray Tune automatically logs all metrics, hyperparameters, and configuration data. To access detailed results:

Access best trial metrics:

In [ ]:
best_trial = analysis.get_best_trial("metrics/mAP50-95(B)", "max", "all")
print(f"Best trial config: {best_trial.config}")
print(f"Best trial final mAP: {best_trial.last_result['metrics/mAP50-95(B)']}")


Plot tuning analysis: Ray Tune has built-in analysis tools. You can visualize results using analysis to compare performance across trials.

In [ ]:
# Plot Ray Tune results
df = analysis.results_df
df.plot(x='training_iteration', y='metrics/mAP50-95(B)', kind='line')
plt.show()

# ViT MNIST

In [ ]:
!pip install torchinfo torch-lr-finder

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import math
from torchvision import datasets, transforms
from torchinfo import summary
from tqdm import tqdm

class Encoder(nn.Module):
    def __init__(self, embed_size = 768, num_heads = 3, dropout = 0.1):
        super().__init__()
        self.norm = nn.LayerNorm(embed_size)
        self.attention = nn.MultiheadAttention(embed_dim=embed_size, num_heads=num_heads, dropout=dropout, batch_first=True)
        self.norm2 = nn.LayerNorm(embed_size)
        self.feedforward = nn.Sequential(
            nn.Linear(embed_size, 4*embed_size),
            nn.GELU(),
            nn.Dropout(dropout),
            nn.Linear(4*embed_size, embed_size),
            nn.Dropout(dropout)
        )
        self.dropout = dropout

    def forward(self, x):
        x = self.norm(x)
        x = x+self.attention(x, x, x)[0]
        x = self.norm2(x)
        x = x+self.feedforward(x)
        return x

class VisionTransformer(nn.Module):
    def __init__(self, in_channels = 3, num_encoders = 6, embed_size = 768, img_size = (324, 324), patch_size = 16, num_classes = 10, num_heads = 4):
        super().__init__()
        self.img_size = img_size
        self.patch_size = patch_size
        num_tokens = (img_size[0]*img_size[1])//(patch_size**2)
        self.class_token = nn.Parameter(torch.randn((embed_size,)))
        self.patch_embedding = nn.Linear(in_channels*patch_size**2,embed_size)
        self.pos_embedding = nn.Parameter(torch.randn((num_tokens+1, embed_size)), requires_grad=True)
        self.encoders = nn.ModuleList([
            Encoder(embed_size=embed_size, num_heads=num_heads) for _ in range(num_encoders)
        ])
        self.mlp_head = nn.Sequential(
            nn.LayerNorm(embed_size),
            nn.Linear(embed_size, num_classes)
        )
    def forward(self, x):
        batch_size, channel_size = x.shape[:2]
        patches = x.unfold(2, self.patch_size, self.patch_size).unfold(3, self.patch_size, self.patch_size)
        patches = patches.contiguous().view(x.size(0), -1, channel_size*self.patch_size*self.patch_size)
        x = self.patch_embedding(patches)
        class_token = self.class_token.unsqueeze(0).repeat(batch_size, 1, 1)
        x = torch.cat([class_token, x], dim=1)
        x = x + self.pos_embedding.unsqueeze(0)
        for encoder in self.encoders:
            x = encoder(x)
        x = x[:,0, :].squeeze()
        x = self.mlp_head(x)
        return x

device = "cuda" if torch.cuda.is_available() else "cpu"
model = VisionTransformer(in_channels=1, img_size=(28, 28), patch_size=7, embed_size=64, num_heads=4, num_encoders=3).to(device)
summary(model, [2, 1, 28, 28])

# dataset
data_transforms = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.1307], std=[0.3081])
])

train_data = datasets.MNIST(root = './data/02/',
                            train=True,
                            download=True,
                            transform=data_transforms)
test_data = datasets.MNIST(root = './data/02/',
                            train=False,
                            download=True,
                            transform=data_transforms)

# find lr
train_dl = torch.utils.data.DataLoader(train_data, batch_size=64, shuffle=True)
test_dl = torch.utils.data.DataLoader(test_data, batch_size=1024, shuffle=False)
optimizer = torch.optim.Adam(lr=5e-4, params=model.parameters())
criterion = nn.CrossEntropyLoss()

lr_finder = LRFinder(model, optimizer, criterion, device="cuda")
lr_finder.range_test(train_dl, end_lr=100, num_iter=100)
lr_finder.plot() # to inspect the loss-learning rate graph
lr_finder.reset() # to reset the model and optimizer to their initial state

# training
# optimizer = torch.optim.Adam(params=model.parameters(), lr=8.52E-03)
epochs = 10
for epoch in range(epochs):
    losses = []
    print(f"Epoch {epoch+1} / {epochs}", end=" ")
    for image, label in tqdm(train_dl):
        image, label = image.to(device), label.to(device)
        pred = model(image)
        loss = criterion(pred, label)
        loss.backward()
        losses.append(loss.item())
        optimizer.step()
        optimizer.zero_grad()
    print(f"loss: {sum(losses) / len(losses)}", end=" ")
    with torch.no_grad():
        cnt, correct_cnt = 0, 0
        for image, label in test_dl:
            image, label = image.to(device), label.to(device)
            pred = model(image).argmax(dim=1)
            cnt += label.shape[0]
            correct_cnt += (pred==label).sum().item()
        print("accuracy: ", correct_cnt / cnt)
torch.save(model.state_dict(), './model.pt')

In [ ]:
# Visualization
import matplotlib.pyplot as plt
with torch.no_grad():
    for image, _ in test_dl:
        image = image[:64]
        image = image.to(device)
        pred = model(image).argmax(dim=1).cpu().detach().numpy()
        image = image.cpu().detach().numpy()
        break
    fig, axes = plt.subplots(8, 8, figsize=(15, 15))
    for i in range(64):
        axes[i//8][i%8].set_title(pred[i])
        axes[i//8][i%8].imshow(image[i][0])